##Movie Review Sentiment Analysis using LSTM RNN 

In [1]:
import pandas as pd

In [2]:
df = pd.read_csv('/content/drive/MyDrive/IMDB Dataset.csv')

In [3]:
df.head()

review sentiment
0  One of the other reviewers has mentioned that ...  positive
1  A wonderful little production. <br /><br />The...  positive
2  I thought this was a wonderful way to spend ti...  positive
3  Basically there's a family where a little boy ...  negative
4  Petter Mattei's "Love in the Time of Money" is...  positive

In [4]:
df.shape

(50000, 2)

In [7]:
#checking the null values
df.isnull().sum()

review       0
sentiment    0
dtype: int64

In [8]:
X = df.drop('sentiment',axis=1)

In [9]:
y = pd.get_dummies(df['sentiment'],drop_first=True)

In [10]:
y.head()

positive
0         1
1         1
2         1
3         0
4         1

In [12]:
X.head()

review
0  One of the other reviewers has mentioned that ...
1  A wonderful little production. <br /><br />The...
2  I thought this was a wonderful way to spend ti...
3  Basically there's a family where a little boy ...
4  Petter Mattei's "Love in the Time of Money" is...

In [13]:
#check the data is biased or not
y.value_counts()

positive
0           25000
1           25000
dtype: int64

In [14]:
import tensorflow as tf
tf.__version__

'2.8.2'

In [15]:
from tensorflow.keras.layers import Embedding
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.models import Sequential
from tensorflow.keras.preprocessing.text import one_hot
from tensorflow.keras.layers import LSTM
from tensorflow.keras.layers import Dense
from tensorflow.keras.layers import Bidirectional
from tensorflow.keras.layers import Dropout

In [16]:
# Vocabulary size
voc_size=15000

##One hot coding for the reviews

In [17]:
comments = X.copy()

In [18]:
comments['review'][0]

"One of the other reviewers has mentioned that after watching just 1 Oz episode you'll be hooked. They are right, as this is exactly what happened with me.<br /><br />The first thing that struck me about Oz was its brutality and unflinching scenes of violence, which set in right from the word GO. Trust me, this is not a show for the faint hearted or timid. This show pulls no punches with regards to drugs, sex or violence. Its is hardcore, in the classic use of the word.<br /><br />It is called OZ as that is the nickname given to the Oswald Maximum Security State Penitentary. It focuses mainly on Emerald City, an experimental section of the prison where all the cells have glass fronts and face inwards, so privacy is not high on the agenda. Em City is home to many..Aryans, Muslims, gangstas, Latinos, Christians, Italians, Irish and more....so scuffles, death stares, dodgy dealings and shady agreements are never far away.<br /><br />I would say the main appeal of the show is due to the fa

In [20]:
comments.reset_index(inplace=True)

In [21]:
import nltk
import re
from nltk.corpus import stopwords

In [22]:
nltk.download('stopwords')

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.


True

In [26]:
nltk.download('omw-1.4')

[nltk_data] Downloading package omw-1.4 to /root/nltk_data...


True

In [28]:
#lemmatizing the reviews

from nltk.stem import WordNetLemmatizer
wordnet=WordNetLemmatizer()
corpus = []
for i in range(0,len(comments)):
    review = re.sub('[^a-zA-Z]', ' ', comments['review'][i])
    review = review.lower()
    review = review.split()
    review = [wordnet.lemmatize(word) for word in review if not word in stopwords.words('english')]
    review = ' '.join(review)
    corpus.append(review)

In [29]:
corpus

['one reviewer mentioned watching oz episode hooked right exactly happened br br first thing struck oz brutality unflinching scene violence set right word go trust show faint hearted timid show pull punch regard drug sex violence hardcore classic use word br br called oz nickname given oswald maximum security state penitentary focus mainly emerald city experimental section prison cell glass front face inwards privacy high agenda em city home many aryan muslim gangsta latino christian italian irish scuffle death stare dodgy dealing shady agreement never far away br br would say main appeal show due fact go show dare forget pretty picture painted mainstream audience forget charm forget romance oz mess around first episode ever saw struck nasty surreal say ready watched developed taste oz got accustomed high level graphic violence violence injustice crooked guard sold nickel inmate kill order get away well mannered middle class inmate turned prison bitch due lack street skill prison exper

In [30]:
onehot_repr=[one_hot(words,voc_size)for words in corpus] 
onehot_repr

[[1592,
  12203,
  12158,
  14161,
  4947,
  953,
  4800,
  653,
  11915,
  5431,
  12742,
  12742,
  8446,
  3556,
  14974,
  4947,
  2284,
  14873,
  1503,
  491,
  5441,
  653,
  8199,
  10741,
  12710,
  14778,
  321,
  10464,
  13296,
  14778,
  2658,
  7845,
  3958,
  13439,
  6111,
  491,
  5732,
  349,
  3366,
  8199,
  12742,
  12742,
  2509,
  4947,
  11209,
  14538,
  13316,
  14077,
  7790,
  7982,
  12253,
  13200,
  10854,
  4807,
  2381,
  7153,
  2044,
  10454,
  12340,
  2549,
  3395,
  1844,
  7941,
  8743,
  935,
  6540,
  8315,
  2381,
  2304,
  9262,
  8981,
  13968,
  3732,
  1647,
  3754,
  3867,
  10273,
  9615,
  6690,
  10456,
  8400,
  12557,
  9656,
  2051,
  6309,
  12381,
  5731,
  12742,
  12742,
  14409,
  9546,
  4321,
  7683,
  14778,
  11651,
  5517,
  10741,
  14778,
  4386,
  110,
  10947,
  8327,
  5906,
  8587,
  2675,
  110,
  12935,
  110,
  5409,
  4947,
  369,
  6491,
  8446,
  953,
  2533,
  4374,
  14974,
  10839,
  1259,
  9546,
  5413,
  1

##Word Embedding

In [31]:
sent_length=200
embedded_docs=pad_sequences(onehot_repr,padding='pre',maxlen=sent_length)
print(embedded_docs)

[[    0     0     0 ...  8914 12665  4774]
 [    0     0     0 ... 13243  4345  6070]
 [    0     0     0 ... 10741  5626  1147]
 ...
 [    0     0     0 ...  1430  7630  5787]
 [    0     0     0 ... 13799  8601  8564]
 [    0     0     0 ...  5792 11452  9386]]


In [32]:
embedded_docs[0]

array([    0,     0,     0,     0,     0,     0,     0,     0,     0,
           0,     0,     0,     0,     0,     0,     0,     0,     0,
           0,     0,     0,     0,     0,     0,     0,     0,     0,
           0,     0,     0,     0,     0,  1592, 12203, 12158, 14161,
        4947,   953,  4800,   653, 11915,  5431, 12742, 12742,  8446,
        3556, 14974,  4947,  2284, 14873,  1503,   491,  5441,   653,
        8199, 10741, 12710, 14778,   321, 10464, 13296, 14778,  2658,
        7845,  3958, 13439,  6111,   491,  5732,   349,  3366,  8199,
       12742, 12742,  2509,  4947, 11209, 14538, 13316, 14077,  7790,
        7982, 12253, 13200, 10854,  4807,  2381,  7153,  2044, 10454,
       12340,  2549,  3395,  1844,  7941,  8743,   935,  6540,  8315,
        2381,  2304,  9262,  8981, 13968,  3732,  1647,  3754,  3867,
       10273,  9615,  6690, 10456,  8400, 12557,  9656,  2051,  6309,
       12381,  5731, 12742, 12742, 14409,  9546,  4321,  7683, 14778,
       11651,  5517,

##Model Creation

In [33]:
embedding_vector_features=400
model=Sequential()
model.add(Embedding(voc_size,embedding_vector_features,input_length=sent_length))
model.add(Bidirectional(LSTM(100)))
model.add(Dropout(0.3))
model.add(Dense(1,activation='sigmoid'))
model.compile(loss='binary_crossentropy',optimizer='adam',metrics=['accuracy'])
print(model.summary())

Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 embedding (Embedding)       (None, 200, 400)          6000000   
                                                                 
 bidirectional (Bidirectiona  (None, 200)              400800    
 l)                                                              
                                                                 
 dropout (Dropout)           (None, 200)               0         
                                                                 
 dense (Dense)               (None, 1)                 201       
                                                                 
Total params: 6,401,001
Trainable params: 6,401,001
Non-trainable params: 0
_________________________________________________________________
None


In [34]:
len(embedded_docs),y.shape

(50000, (50000, 1))

In [35]:
import numpy as np
X_final=np.array(embedded_docs)
y_final=np.array(y)

In [36]:
X_final.shape,y_final.shape

((50000, 200), (50000, 1))

In [37]:
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X_final, y_final, test_size=0.33, random_state=42)

##model Training

In [38]:
callback = tf.keras.callbacks.EarlyStopping(
    monitor='val_loss',
    min_delta=0,
    patience=0,
    verbose=0,
    mode='auto',
    baseline=None,
    restore_best_weights=False
)

In [39]:
model.fit(X_train,y_train,validation_data=(X_test,y_test),epochs=10,batch_size=64,callbacks=[callback])

Epoch 1/10
524/524 [==============================] - 29s 38ms/step - loss: 0.3781 - accuracy: 0.8322 - val_loss: 0.3284 - val_accuracy: 0.8673
Epoch 2/10
524/524 [==============================] - 19s 36ms/step - loss: 0.2365 - accuracy: 0.9086 - val_loss: 0.3186 - val_accuracy: 0.8705


##Performance and Accuracy

In [42]:
y_pred=(model.predict(X_test) > 0.5).astype("int32")

In [43]:
from sklearn.metrics import confusion_matrix
confusion_matrix(y_test,y_pred)

array([[6902, 1306],
       [ 831, 7461]])

In [44]:
from sklearn.metrics import accuracy_score
accuracy_score(y_test,y_pred)

0.8704848484848485

In [45]:
from sklearn.metrics import classification_report
print(classification_report(y_test,y_pred))

              precision    recall  f1-score   support

           0       0.89      0.84      0.87      8208
           1       0.85      0.90      0.87      8292

    accuracy                           0.87     16500
   macro avg       0.87      0.87      0.87     16500
weighted avg       0.87      0.87      0.87     16500



In [46]:
import pickle

In [47]:
pickle.dump(model, open('model.pkl', 'wb'))